In [10]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import scipy
from tqdm import tqdm_notebook as tqdm
import string

%matplotlib inline

plt.style.use('seaborn-deep')
plt.rcParams['figure.figsize'] = (12,8)

In [2]:
df_train = pd.read_csv('train.tsv', sep='\t', index_col=0)
df_test = pd.read_csv('test_nolabel.tsv', sep='\t', index_col=0)

In [3]:
with open('lemmatized_train_description.csv', 'r') as f:
    df_train['lem_desc_text'] = f.read().split('\n')[:-1]
with open('lemmatized_train_name.csv', 'r') as f:
    df_train['lem_name_text'] = f.read().split('\n')[:-1]
with open('lemmatized_test_description.csv', 'r') as f:
    df_test['lem_desc_text'] = f.read().split('\n')[:-1]
with open('lemmatized_test_name.csv', 'r') as f:
    df_test['lem_name_text'] = f.read().split('\n')[:-1]

In [4]:
df_train.head()

category_id             city date_created  delivery_available  \
1             4        Краснодар   2018-10-08               False   
2             4           Тюмень   2018-06-18               False   
4             9             Омск   2018-07-31                True   
6             3  Санкт-Петербург   2018-04-17               False   
10            5           Москва   2018-02-09               False   

                                            desc_text  img_num      lat  \
1   Продаю стол раскладной, деревянный, советский ...        3  45.0686   
2   Тарелки глубокие 6 шт. Блюдца, чашки по 6 шт. ...        2  57.1840   
4   Новый,с этикеткой. Размер L. Не подошёл по раз...        1  54.9889   
6   Складывается тростью, все колеса вниз. Сплошна...        4  59.9590   
10  Неразлучники, птичкам по 1,5 года. Продаю с бо...        2  55.6473   

       long          name_text                          owner_id  \
1   38.9518               Стол  4ce583fe8231a0cc4a3c7d241c7d0289   
2   65.5674             Посуда  e58be2c8f143c17246dc2243b5d3b98f   
4   73.4312             Костюм  51b408796027214232532b7e478e2159   
6   30.4877            Коляска  6544b83acbbf04439a7ba983093cafb4   
10  37.4118  Волнистые попугаи  ea575e28daf1f47bfce63015cd3ce5cf   

          ...           price                        product_id product_type  \
1         ...           500.0  8cb80c05c65c210275f5500779d6b593            1   
2         ...           300.0  3b7a9f8b27a53b63525f95bc8070abb2            1   
4         ...          1100.0  c97dd9c5a3e938c52cf5d7822bc0eb7b            1   
6         ...          5000.0  3e5d0286b25fd7f62f88bc436a59ae4e            1   
10        ...          2000.0  57b4a8679d0d3eb1e31367b57221098f            1   

                                           properties                 region  \
1   [{'slug_id': 'stoly_stulya_tip', 'slug_name': ...     Краснодарский край   
2   [{'slug_id': 'dom_dacha_posuda_tip', 'slug_nam...      Тюменская область   
4   [{'slug_id': 'zhenskaya_odezhda_pidzhaki_kosty...         Омская область   
6   [{'slug_id': 'waggon_type', 'slug_name': 'Тип'...  Ленинградская область   
10                                                 []     Московская область   

   sold_mode  subcategory_id  sold_fast  \
1          1             410          1   
2          1             405          0   
4          1             908          0   
6          1             312          0   
10         1             504          0   

                                        lem_desc_text      lem_name_text  
1   продавать стол раскладной деревянный советский...               стол  
2   тарелка глубокий 6 шт блюдце чашка 6 шт весь р...             посуда  
4   новый этикетка размер l подойти размер маломер...             костюм  
6   складываться трость весь колесо вниз сплошной ...            коляска  
10  неразлучник птичка 1 5 год продавать большой к...  волнистый попугай  

[5 rows x 21 columns]

In [5]:
X = df_train.drop(['sold_fast', 'product_id', 'date_created', 'owner_id', 'category_id', 'city'], axis=1)
y = df_train['sold_fast']

In [6]:
X.columns.values

array(['delivery_available', 'desc_text', 'img_num', 'lat', 'long',
       'name_text', 'payment_available', 'price', 'product_type',
       'properties', 'region', 'sold_mode', 'subcategory_id',
       'lem_desc_text', 'lem_name_text'], dtype=object)

In [7]:
features = ['delivery_available', 'img_num', 'lat', 'long', 'payment_available', 'price', 'product_type', 'sold_mode', 'subcategory_id']
len(features)

9

In [18]:
df_train['properties'].values[31].split('}')[:-1]

["[{'slug_id': 'realty_obshaya_ploshad', 'slug_name': 'Общая площадь (realty_obshaya_ploshad)', 'value': '200', 'value_id': 200",
 ", {'slug_id': 'realty_infrastructure', 'slug_name': 'Инфраструктура около дома (realty_infrastructure)', 'value': 'Детская площадка', 'value_id': 12027",
 ", {'slug_id': 'realty_infrastructure', 'slug_name': 'Инфраструктура около дома (realty_infrastructure)', 'value': 'Транспорт', 'value_id': 12033",
 ", {'slug_id': 'realty_infrastructure', 'slug_name': 'Инфраструктура около дома (realty_infrastructure)', 'value': 'Спорт', 'value_id': 12032",
 ", {'slug_id': 'realty_infrastructure', 'slug_name': 'Инфраструктура около дома (realty_infrastructure)', 'value': 'Магазины', 'value_id': 12031",
 ", {'slug_id': 'realty_infrastructure', 'slug_name': 'Инфраструктура около дома (realty_infrastructure)', 'value': 'Развлечения', 'value_id': 12035",
 ", {'slug_id': 'realty_infrastructure', 'slug_name': 'Инфраструктура около дома (realty_infrastructure)', 'value': 'Кафе

In [19]:
list(map(lambda x: x[x.find('{'):].split(','), df_train['properties'].values[31].split('}')[:-1]))

[["{'slug_id': 'realty_obshaya_ploshad'",
  " 'slug_name': 'Общая площадь (realty_obshaya_ploshad)'",
  " 'value': '200'",
  " 'value_id': 200"],
 ["{'slug_id': 'realty_infrastructure'",
  " 'slug_name': 'Инфраструктура около дома (realty_infrastructure)'",
  " 'value': 'Детская площадка'",
  " 'value_id': 12027"],
 ["{'slug_id': 'realty_infrastructure'",
  " 'slug_name': 'Инфраструктура около дома (realty_infrastructure)'",
  " 'value': 'Транспорт'",
  " 'value_id': 12033"],
 ["{'slug_id': 'realty_infrastructure'",
  " 'slug_name': 'Инфраструктура около дома (realty_infrastructure)'",
  " 'value': 'Спорт'",
  " 'value_id': 12032"],
 ["{'slug_id': 'realty_infrastructure'",
  " 'slug_name': 'Инфраструктура около дома (realty_infrastructure)'",
  " 'value': 'Магазины'",
  " 'value_id': 12031"],
 ["{'slug_id': 'realty_infrastructure'",
  " 'slug_name': 'Инфраструктура около дома (realty_infrastructure)'",
  " 'value': 'Развлечения'",
  " 'value_id': 12035"],
 ["{'slug_id': 'realty_infrast

In [34]:
prop_col = []
for i, item_prop in enumerate(df_train['properties'].values):
    prop_text = []
    for text in item_prop.split('}')[:-1]:
        props = text[text.find('{'):].split(',')
        name = props[1][props[1].find(': '):].translate(str.maketrans('','',string.punctuation))
        val = props[2][props[2].find(': '):].translate(str.maketrans('','',string.punctuation))
        if 'Нет' not in val:
#             prop_text.append(name)
            if 'Есть' not in val:
                prop_text.append(val)
    prop_col.append(' '.join(prop_text))

In [35]:
prop_col

[' Столы',
 ' Тарелки',
 ' Костюмы с юбкой  4648 L',
 ' Прогулочная  До 3 лет',
 '',
 ' Зеленый  Городские',
 ' Шотландская',
 ' Samsung  ЖК  От 30 до 349',
 ' Дорожные мотоциклы',
 ' Пищевое',
 ' Отдельно стоящие  LG',
 ' Стульчики для кормления',
 ' Для автомобилей',
 ' Спортивные  PlayStation З',
 '',
 ' Палки для треккинга',
 '',
 ' Розовый  Демисезон  22  Девочкам  Ботинки',
 ' Шкафы',
 '',
 '',
 ' Овчарка',
 '',
 '',
 ' Сумкикенгуру',
 '',
 ' Бюстгальтеры  Черный',
 ' Сандалии  Девочкам',
 ' Холодильники  Отдельно стоящие  Stinol',
 ' Samsung  ЖК  От 40 до 449',
 ' От 5 до 99 Мпикс  1  32 Гб  iOS  Apple  5 Мпикс и более',
 ' 200  Детская площадка  Транспорт  Спорт  Магазины  Развлечения  Кафе и рестораны  Собственник  Совмещенный  Лоджия  100  1 комната  На длит срок  Не включены  9  Косметический  1 месяц  1',
 ' Детское питание',
 '',
 ' Настольные',
 ' 4446 М  Трусы',
 ' Пеленальные столики',
 ' Беспроводные  Накладные',
 ' Тойтерьер',
 ' Сапоги  Черный  42',
 ' Статуэтки',
 '

In [39]:
list(map(lambda x: x.split(','), df_train.iloc[29944].properties.split('}')[:-1]))

[["[{'slug_id': 'auto_engine_vol'",
  " 'slug_name': 'Округленный объем двигателя в литрах'",
  " 'value': '1600'",
  " 'value_id': 1600"],
 ['',
  " {'slug_id': 'auto_car_cleared'",
  " 'slug_name': 'Растаможен'",
  " 'value': 'Да'",
  " 'value_id': 20752"],
 ['',
  " {'slug_id': 'auto_gear_type'",
  " 'slug_name': 'Тип коробки передач'",
  " 'value': 'Автомат'",
  " 'value_id': 20810"],
 ['',
  " {'slug_id': 'auto_owners_by_pts'",
  " 'slug_name': 'Количество владельцев по ПТС'",
  " 'value': '2'",
  " 'value_id': 2"],
 ['',
  " {'slug_id': 'auto_doors_count'",
  " 'slug_name': 'Количество дверей'",
  " 'value': '5'",
  " 'value_id': 5"],
 ['',
  " {'slug_id': 'auto_drive_type'",
  " 'slug_name': 'Тип привода'",
  " 'value': 'Передний'",
  " 'value_id': 20803"],
 ['',
  " {'slug_id': 'auto_model'",
  " 'slug_name': 'Модель автомобиля'",
  ' \'value\': "Cee\'d"',
  " 'value_id': 13147"],
 ['',
  " {'slug_id': 'auto_generation'",
  " 'slug_name': 'Название поколения автомобиля'",
  " '

In [24]:
new_col = []
for i, item_prop in enumerate(df_train.properties.values):
    try:
        item_prop = item_prop.replace('"', '').replace('\'', '"')
        j = [json.loads(item_prop)]
        new_col.append(' '.join([a["slug_name"] + ' ' + a["value"] for a in j[0]]))
    except:
#         print(item_prop)
        print(item_prop.replace('"', '').replace('\'', '"'))
        print(i)

[{slug_id: televizory_marka, slug_name: Марка, value: Samsung, value_id: 9612}, {slug_id: televizory_tip, slug_name: Тип, value: ЖК, LED, value_id: 9588}, {slug_id: televizory_diagonal_ekrana, slug_name: Диагональ экрана, value: От 30 до 34.9, value_id: 9625}]
7
[{slug_id: televizory_marka, slug_name: Марка, value: Samsung, value_id: 9612}, {slug_id: televizory_tip, slug_name: Тип, value: ЖК, LED, value_id: 9588}, {slug_id: televizory_diagonal_ekrana, slug_name: Диагональ экрана, value: От 40 до 44.9, value_id: 9627}, {slug_id: televizory_smart_tv, slug_name: Smart TV, value: Есть, value_id: 9632}]
29
[{slug_id: smartfony_diagonal_ekrana, slug_name: Диагональ экрана, value: От 5 до 5.4, value_id: 8938}, {slug_id: smartfony_slot_dlya_karty_pamyaty, slug_name: Слот для карты памяти, value: Есть, value_id: 8948}, {slug_id: smartfony_podderzhka_bezkontaktnyh_platezhei, slug_name: NFC, value: Нет, value_id: 8971}, {slug_id: smartfony_gps, slug_name: GPS, value: Есть, value_id: 8968}, {slug_

[{slug_id: monitory_marka, slug_name: Марка, value: Viewsonic, value_id: 9280}, {slug_id: monitory_diagonal_ekrana, slug_name: Диагональ экрана, value: 30 и более, value_id: 9298}]
13186
[{slug_id: smartfony_diagonal_ekrana, slug_name: Диагональ экрана, value: От 5 до 5.4, value_id: 8938}, {slug_id: smartfony_vstroennaya_pamyat, slug_name: Встроенная память, value: 16 Гб, value_id: 8943}, {slug_id: smartfony_slot_dlya_karty_pamyaty, slug_name: Слот для карты памяти, value: Есть, value_id: 8948}, {slug_id: smartfony_4g_lte, slug_name: 4G LTE, value: Есть, value_id: 8962}, {slug_id: smartfony_kolichestvo_sim_kart, slug_name: Количество SIM-карт, value: 2, value_id: 8965}, {slug_id: phone_brand, slug_name: Марка, value: Samsung, value_id: 8916}, {slug_id: smartfony_os, slug_name: Операционная система, value: Android, value_id: 8929}, {slug_id: smartfony_osnovnaya_kamera, slug_name: Основная камера, value: От 5 до 9.9 Мпикс, value_id: 8953}, {slug_id: smartfony_frontalnaya_kamera, slug_nam

[{slug_id: smartfony_os, slug_name: Операционная система, value: Android, value_id: 8929}, {slug_id: phone_brand, slug_name: Марка, value: Samsung, value_id: 8916}, {slug_id: smartfony_diagonal_ekrana, slug_name: Диагональ экрана, value: От 4.1 до 4.9, value_id: 8937}, {slug_id: smartfony_vstroennaya_pamyat, slug_name: Встроенная память, value: 8 Гб, value_id: 8942}, {slug_id: smartfony_frontalnaya_kamera, slug_name: Фронтальная камера, value: От 1 до 2.9 Мпикс, value_id: 8957}, {slug_id: smartfony_osnovnaya_kamera, slug_name: Основная камера, value: От 5 до 9.9 Мпикс, value_id: 8953}, {slug_id: smartfony_3g, slug_name: 3G, value: Есть, value_id: 8960}, {slug_id: smartfony_4g_lte, slug_name: 4G LTE, value: Есть, value_id: 8962}, {slug_id: smartfony_gps, slug_name: GPS, value: Есть, value_id: 8968}, {slug_id: smartfony_slot_dlya_karty_pamyaty, slug_name: Слот для карты памяти, value: Есть, value_id: 8948}, {slug_id: smartfony_podderzhka_bezkontaktnyh_platezhei, slug_name: NFC, value: Не

41876
[{slug_id: notebook_brand, slug_name: Марка, value: ASUS, value_id: 9242}, {slug_id: notebook_diagonal_ekrana, slug_name: Диагональ экрана, value: 16.5 и более, value_id: 9261}, {slug_id: notebook_tip, slug_name: Тип, value: Ноутбуки, value_id: 9236}]
41886
[{slug_id: phone_brand, slug_name: Марка, value: Apple, value_id: 8889}, {slug_id: smartfony_osnovnaya_kamera, slug_name: Основная камера, value: От 5 до 9.9 Мпикс, value_id: 8953}, {slug_id: smartfony_podderzhka_bezkontaktnyh_platezhei, slug_name: NFC, value: Есть, value_id: 8970}, {slug_id: smartfony_diagonal_ekrana, slug_name: Диагональ экрана, value: 5.5 и более, value_id: 8939}, {slug_id: smartfony_frontalnaya_kamera, slug_name: Фронтальная камера, value: 5 Мпикс и более, value_id: 8959}, {slug_id: smartfony_kolichestvo_sim_kart, slug_name: Количество SIM-карт, value: 1, value_id: 8964}, {slug_id: smartfony_4g_lte, slug_name: 4G LTE, value: Есть, value_id: 8962}, {slug_id: smartfony_zashchita_ot_pili_i_vlagi, slug_name: З

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



205458
[{slug_id: smartfony_kolichestvo_sim_kart, slug_name: Количество SIM-карт, value: 2, value_id: 8965}, {slug_id: smartfony_frontalnaya_kamera, slug_name: Фронтальная камера, value: 5 Мпикс и более, value_id: 8959}, {slug_id: smartfony_os, slug_name: Операционная система, value: Android, value_id: 8929}, {slug_id: smartfony_3g, slug_name: 3G, value: Есть, value_id: 8960}, {slug_id: smartfony_4g_lte, slug_name: 4G LTE, value: Есть, value_id: 8962}, {slug_id: smartfony_gps, slug_name: GPS, value: Есть, value_id: 8968}, {slug_id: smartfony_podderzhka_bezkontaktnyh_platezhei, slug_name: NFC, value: Есть, value_id: 8970}, {slug_id: smartfony_slot_dlya_karty_pamyaty, slug_name: Слот для карты памяти, value: Есть, value_id: 8948}, {slug_id: phone_brand, slug_name: Марка, value: Samsung, value_id: 8916}, {slug_id: smartfony_diagonal_ekrana, slug_name: Диагональ экрана, value: 5.5 и более, value_id: 8939}, {slug_id: smartfony_osnovnaya_kamera, slug_name: Основная камера, value: 10 Мпикс и 

[{slug_id: smartfony_diagonal_ekrana, slug_name: Диагональ экрана, value: От 5 до 5.4, value_id: 8938}, {slug_id: phone_brand, slug_name: Марка, value: Lenovo, value_id: 8907}, {slug_id: smartfony_os, slug_name: Операционная система, value: Android, value_id: 8929}, {slug_id: smartfony_vstroennaya_pamyat, slug_name: Встроенная память, value: 8 Гб, value_id: 8942}]
218505
[{slug_id: velosipedy_tip, slug_name: Тип, value: Городские, дорожные, value_id: 10173}, {slug_id: velosipedy_rama_rost, slug_name: Рама / Рост велосипедиста, value: 13 (130-145 см), value_id: 10205}, {slug_id: sport_tzvet, slug_name: Цвет, value: Зеленый, value_id: 10188}]
218541
[{slug_id: phone_brand, slug_name: Марка, value: Samsung, value_id: 8916}, {slug_id: smartfony_slot_dlya_karty_pamyaty, slug_name: Слот для карты памяти, value: Есть, value_id: 8948}, {slug_id: smartfony_os, slug_name: Операционная система, value: Android, value_id: 8929}, {slug_id: smartfony_diagonal_ekrana, slug_name: Диагональ экрана, valu

[{slug_id: smartfony_os, slug_name: Операционная система, value: Android, value_id: 8929}, {slug_id: smartfony_kolichestvo_sim_kart, slug_name: Количество SIM-карт, value: 2, value_id: 8965}, {slug_id: smartfony_4g_lte, slug_name: 4G LTE, value: Есть, value_id: 8962}, {slug_id: smartfony_podderzhka_bezkontaktnyh_platezhei, slug_name: NFC, value: Есть, value_id: 8970}, {slug_id: smartfony_diagonal_ekrana, slug_name: Диагональ экрана, value: От 5 до 5.4, value_id: 8938}, {slug_id: smartfony_slot_dlya_karty_pamyaty, slug_name: Слот для карты памяти, value: Есть, value_id: 8948}, {slug_id: smartfony_gps, slug_name: GPS, value: Есть, value_id: 8968}]
230090
[{slug_id: notebook_diagonal_ekrana, slug_name: Диагональ экрана, value: от 15 до 16.4, value_id: 9260}, {slug_id: notebook_brand, slug_name: Марка, value: HP, value_id: 9248}, {slug_id: notebook_tip, slug_name: Тип, value: Ноутбуки, value_id: 9236}]
230095
[{slug_id: smartfony_3g, slug_name: 3G, value: Есть, value_id: 8960}, {slug_id: s

242456
[{slug_id: smartfony_diagonal_ekrana, slug_name: Диагональ экрана, value: 5.5 и более, value_id: 8939}, {slug_id: smartfony_vstroennaya_pamyat, slug_name: Встроенная память, value: 16 Гб, value_id: 8943}, {slug_id: phone_brand, slug_name: Марка, value: Huawei, value_id: 8904}, {slug_id: smartfony_slot_dlya_karty_pamyaty, slug_name: Слот для карты памяти, value: Есть, value_id: 8948}, {slug_id: smartfony_kolichestvo_sim_kart, slug_name: Количество SIM-карт, value: 2, value_id: 8965}, {slug_id: smartfony_gps, slug_name: GPS, value: Есть, value_id: 8968}, {slug_id: smartfony_zashchita_ot_pili_i_vlagi, slug_name: Защита от пыли и влаги, value: Нет, value_id: 8973}, {slug_id: smartfony_4g_lte, slug_name: 4G LTE, value: Есть, value_id: 8962}, {slug_id: smartfony_frontalnaya_kamera, slug_name: Фронтальная камера, value: 5 Мпикс и более, value_id: 8959}, {slug_id: smartfony_3g, slug_name: 3G, value: Есть, value_id: 8960}, {slug_id: smartfony_os, slug_name: Операционная система, value: A

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [12]:
X['properties'].iloc[0]

"[{'slug_id': 'stoly_stulya_tip', 'slug_name': 'Тип', 'value': 'Столы', 'value_id': 9490}]"

In [11]:
X['properties'].iloc[0].split('}')[:-1]

["[{'slug_id': 'stoly_stulya_tip', 'slug_name': 'Тип', 'value': 'Столы', 'value_id': 9490"]

In [9]:
X['properties'].iloc[:10].tolist()

["[{'slug_id': 'stoly_stulya_tip', 'slug_name': 'Тип', 'value': 'Столы', 'value_id': 9490}]",
 "[{'slug_id': 'dom_dacha_posuda_tip', 'slug_name': 'Тип', 'value': 'Тарелки', 'value_id': 9461}]",
 "[{'slug_id': 'zhenskaya_odezhda_pidzhaki_kostyumy_tip', 'slug_name': 'Тип', 'value': 'Костюмы с юбкой', 'value_id': 8362}, {'slug_id': 'zhenskaya_odezhda_razmer', 'slug_name': 'Размер', 'value': '46-48 (L)', 'value_id': 8290}]",
 "[{'slug_id': 'waggon_type', 'slug_name': 'Тип', 'value': 'Прогулочная', 'value_id': 8615}, {'slug_id': 'waggon_max_age', 'slug_name': 'Возраст', 'value': 'До 3 лет', 'value_id': 8620}]",
 '[]',
 "[{'slug_id': 'sport_tzvet', 'slug_name': 'Цвет', 'value': 'Зеленый', 'value_id': 10188}, {'slug_id': 'velosipedy_tip', 'slug_name': 'Тип', 'value': 'Городские, дорожные', 'value_id': 10173}]",
 "[{'slug_id': 'koshki_poroda', 'slug_name': 'Порода', 'value': 'Шотландская', 'value_id': 10437}]",
 '[{\'slug_id\': \'televizory_marka\', \'slug_name\': \'Марка\', \'value\': \'Samsu

In [197]:
from sklearn.model_selection import train_test_split

X_train, X_val, y_train, y_val = train_test_split(X, y, test_size=0.33, random_state=42)

In [254]:
from sklearn.base import BaseEstimator, TransformerMixin
from itertools import combinations, chain


class Cat2Proba(BaseEstimator, TransformerMixin):
    def __init__(self, keys, ngram=1):
        self.keys = keys
        self.combs = list(chain(*map(lambda x: combinations(keys, x), range(1, ngram+1))))
        self.ngram = ngram
        self.cat_dicts = {}
        self.cat_av = {}
        
    @staticmethod
    def values(comb, X):
        return np.array(list(map(lambda x: ' '.join(list(map(str, x))), X[list(comb)].values)))
    
    @staticmethod
    def cat2proba_dict(values, labels):
        cat_dict = {}
        probas = []
        for aval in np.unique(values):
            labels_for_val = labels[values == aval]
            cat_dict[aval] = float(len(labels_for_val[labels_for_val == 1])) / len(labels_for_val)
        return cat_dict
    
    @staticmethod
    def cat2proba(cat_dict, cat_av, values):
        probas = []
        for aval in values:
            if aval in cat_dict:
                probas.append(cat_dict[aval])
            else:
                probas.append(cat_av)
        return np.array(probas)
    
    def fit(self, X, y):
        for comb in tqdm(self.combs):
            self.cat_dicts[comb] = Cat2Proba.cat2proba_dict(Cat2Proba.values(comb, X), y)
            self.cat_av[comb] = np.average(list(self.cat_dicts[comb].values()))
        return self
    
    def transform(self, X, y=None):
        return np.array([Cat2Proba.cat2proba(
            self.cat_dicts[comb],
            self.cat_av[comb],
            Cat2Proba.values(comb, X)
        ) for comb in self.combs]).T

In [264]:
# %%time
# cat2proba = Cat2Proba([
# #     'city',
#     'delivery_available',
#     'payment_available',
#     'product_type',
#     'sold_mode',
#     'subcategory_id'], 2)
# cat2proba.fit(X_train1, y_train1)

CPU times: user 14.9 s, sys: 24.1 ms, total: 14.9 s
Wall time: 12.6 s


In [265]:
from scipy.sparse import hstack

def preprocessing(data):
    
    x1 = data[features].values
    return np.concatenate([x1], axis=1)

In [266]:
X_train_prep = preprocessing(X_train)
X_val_prep = preprocessing(X_val)
X_train_prep.shape, X_val_prep.shape

((70608, 24), (115923, 24))

# model

In [267]:
from xgboost import XGBClassifier

model = XGBClassifier(n_estimators=200, learning_rate=0.02, max_depth=8, n_jobs=3, colsample_bytree=0.7, scale_pos_weight=1., verbosity=3)
model.fit(X_train2_prep, y_train2)

[16:56:04] INFO: /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 352 extra nodes, 0 pruned nodes, max_depth=8
[16:56:04] INFO: /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 364 extra nodes, 0 pruned nodes, max_depth=8
[16:56:04] INFO: /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 344 extra nodes, 0 pruned nodes, max_depth=8
[16:56:04] INFO: /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 366 extra nodes, 0 pruned nodes, max_depth=8
[16:56:05] INFO: /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 388 extra nodes, 0 pruned nodes, max_depth=8
[16:56:05] INFO: /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 330 extra nodes, 0 pruned nodes, max_depth=8
[16:56:05] INFO: /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 346 extra nodes, 0 pruned nodes, max_depth=8
[16:56:05] INFO: /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 376 e

[16:56:10] INFO: /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 378 extra nodes, 0 pruned nodes, max_depth=8
[16:56:10] INFO: /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 330 extra nodes, 0 pruned nodes, max_depth=8
[16:56:10] INFO: /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 318 extra nodes, 0 pruned nodes, max_depth=8
[16:56:10] INFO: /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 362 extra nodes, 0 pruned nodes, max_depth=8
[16:56:10] INFO: /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 338 extra nodes, 0 pruned nodes, max_depth=8
[16:56:10] INFO: /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 240 extra nodes, 0 pruned nodes, max_depth=8
[16:56:10] INFO: /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 382 extra nodes, 0 pruned nodes, max_depth=8
[16:56:10] INFO: /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 352 e

[16:56:14] INFO: /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 314 extra nodes, 0 pruned nodes, max_depth=8
[16:56:14] INFO: /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 296 extra nodes, 0 pruned nodes, max_depth=8
[16:56:14] INFO: /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 320 extra nodes, 0 pruned nodes, max_depth=8
[16:56:14] INFO: /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 304 extra nodes, 0 pruned nodes, max_depth=8
[16:56:14] INFO: /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 234 extra nodes, 0 pruned nodes, max_depth=8
[16:56:15] INFO: /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 270 extra nodes, 0 pruned nodes, max_depth=8
[16:56:15] INFO: /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 292 extra nodes, 0 pruned nodes, max_depth=8
[16:56:15] INFO: /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 264 e

[16:56:18] INFO: /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 144 extra nodes, 0 pruned nodes, max_depth=8


XGBClassifier(base_score=0.5, booster='gbtree', colsample_bylevel=1,
       colsample_bynode=1, colsample_bytree=0.7, gamma=0,
       learning_rate=0.02, max_delta_step=0, max_depth=8,
       min_child_weight=1, missing=None, n_estimators=200, n_jobs=3,
       nthread=None, objective='binary:logistic', random_state=0,
       reg_alpha=0, reg_lambda=1, scale_pos_weight=1.0, seed=None,
       silent=None, subsample=1, verbosity=3)

In [268]:
from sklearn.metrics import roc_auc_score

print("train AUC: ", roc_auc_score(y_train2, model.predict_proba(X_train2_prep)[:, 1]))
print("train AUC: ", roc_auc_score(y_train1, model.predict_proba(X_train1_prep)[:, 1]))
print("val AUC: ", roc_auc_score(y_val, model.predict_proba(X_val_prep)[:, 1]))

train AUC:  0.7018822951108701
train AUC:  0.6161043052692408
val AUC:  0.614210414072785


In [263]:
sorted(enumerate(model.feature_importances_), key=lambda x: -x[1])

[(26, 0.12236511),
 (31, 0.090490885),
 (27, 0.06593329),
 (20, 0.058080718),
 (5, 0.042291407),
 (33, 0.03755527),
 (30, 0.031394687),
 (32, 0.030988982),
 (23, 0.03035114),
 (11, 0.02957806),
 (12, 0.029067313),
 (22, 0.028170489),
 (13, 0.026782475),
 (19, 0.026369119),
 (16, 0.026367445),
 (25, 0.026064727),
 (6, 0.024895338),
 (29, 0.024096377),
 (28, 0.024013625),
 (8, 0.023344487),
 (7, 0.021636978),
 (17, 0.02130592),
 (3, 0.021177271),
 (2, 0.02075991),
 (15, 0.018705467),
 (4, 0.018153662),
 (1, 0.017034953),
 (0, 0.016539171),
 (10, 0.01610603),
 (14, 0.015881795),
 (9, 0.0144978445),
 (18, 0.0),
 (21, 0.0),
 (24, 0.0)]

In [ ]:
# train AUC:  0.6491806432723649
# val AUC:  0.6202890915933602